<h1>Taller #2: Cálculo del número de generadores del Grupo Cíclico de G</h1>

<h4> Presentado por: David Santiago Cruz Hernandez</h4>
<h4> Asignatura: Matemáticas Discretas II </h4>

In [93]:
import time
numGeneradoresGCiclico = 0
dicDescomposicionPrimosGrupo = {}

In [94]:
def bold(texto):
    return "\033[1m" + texto + "\033[0m"

In [95]:
def obtenerDigitoSuperIndice(indice):
    if indice == 1:
        return str(chr(0x00b9))
    elif 2 <= indice <= 3:
        return str(chr(0x00b0 + indice))
    else:
        return str(chr(0x2070 + indice))


In [96]:
def imprimirSuperIndice(numGenerador):
    strIndice = ""
    for digit in str(numGenerador):
        strIndice = strIndice + obtenerDigitoSuperIndice(int(digit))
    return strIndice

#### Ingreso de N:

In [97]:
n = int(input("Ingrese el Orden de G:"))

In [98]:
Grupo = []
for num in range(1,n+1):
    Grupo.append(num)

### Metodo Alternativo:
##### Comprobación por medio del siguiente *Lema*:

###### • **i)** φ(I) = 1
###### • **ii)** Si *p* es **primo**, entonces el **φ($p^{a}$) =** $p^{a}$ - $p^{a-1}$
###### • **iii)** Si *mcd(m,n)* = 1, entonces el **φ(m•n) =** φ(m) + φ(n)

In [99]:
def calcularDescomposicionPrimos(resultadoDivision,dicDescomposicionPrimos):
    potencia = 1
    for divisor in range(2,len(Grupo)):
        while resultadoDivision%divisor==0:
            resultadoDivision = resultadoDivision/divisor
            if divisor not in dicDescomposicionPrimos:
                potencia = 1
            dicDescomposicionPrimos[divisor] = potencia
            potencia+=1
        if resultadoDivision ==1:
            break
    return dicDescomposicionPrimos

In [100]:
def LemaTotientEulerPrimos():
    resultado = 1
    for primo in dicDescomposicionPrimosGrupo:
        indice = dicDescomposicionPrimosGrupo.get(primo)
        resultado = resultado * (pow(primo,indice) - pow(primo,indice-1))
    return resultado


In [101]:
def imprimirCadenaDescomposicion():
    strDescomposicion = ""
    for base in dicDescomposicionPrimosGrupo:
        strIndice = imprimirSuperIndice(dicDescomposicionPrimosGrupo[base])
        strDescomposicion = strDescomposicion + str(base) + strIndice + "•"
    return strDescomposicion[0:-1]


In [102]:
def imprimirCadenaDescomposicionTotient():
    strLemaIII = ""
    for potencia in imprimirCadenaDescomposicion().split("•"):
        strLemaIII = strLemaIII + "φ(" + potencia + ")•"

    strLemaII = ""
    for base in dicDescomposicionPrimosGrupo:
        strLemaII = strLemaII + "(" + str(base) + imprimirSuperIndice(dicDescomposicionPrimosGrupo[base]) + "-" + str(base) + imprimirSuperIndice(dicDescomposicionPrimosGrupo[base] - 1) + ")•"
    return strLemaIII[0:-1] + " = " + strLemaII[0:-1]

In [103]:
def imprimirMetodoAlternativo():
    print("                    " + bold("Orden del Grupo G: " + str(n)) + "\n")
    print("Tiempo de ejecución del Metodo Alternativo: " + str(Tiempo2) + " segundos.")
    print("→ Descomposición de Factores Primos de " + bold("n") + ": " + imprimirCadenaDescomposicion())
    print(bold("→ Número de Generadores Cíclicos de G:"))
    print("      φ(" + str(n) + ") = φ(" + imprimirCadenaDescomposicion() + ") = " + imprimirCadenaDescomposicionTotient() + " = " + str(numGeneradoresGCiclico) )
    print("→ Por este Metodo, no se obtiene la lista de los Generadores Cíclicos de G, ni los SubGrupos generados.")

###### Ejecutar el Metodo Alternativo:

In [104]:
inicio2 = time.time()
dicDescomposicionPrimosGrupo = calcularDescomposicionPrimos(len(Grupo), {})
numGeneradoresGCiclico = LemaTotientEulerPrimos()

fin2 = time.time()
Tiempo2 = round(fin2-inicio2,4)

imprimirMetodoAlternativo()

                    Orden del Grupo G: 51200

Tiempo de ejecución del Metodo Alternativo: 0.0 segundos.
→ Descomposición de Factores Primos de n: 2¹¹•5²
→ Número de Generadores Cíclicos de G:
      φ(51200) = φ(2¹¹•5²) = φ(2¹¹)•φ(5²) = (2¹¹-2¹⁰)•(5²-5¹) = 20480
→ Por este Metodo, no se obtiene la lista de los Generadores Cíclicos de G, ni los SubGrupos generados.


### Método Totient de Euler:
##### Comprobación de cada elemento de G. Si mcd(x,n) = 1, entonces ese elemento genera un Grupo Cíclico:

In [105]:
def calcularMCDconGrupo(numGenerador):
    listaPrimosComunes = []
    mcd = 1
    descPrimosNumGenerador = calcularDescomposicionPrimos(numGenerador, {})
    menorRepeticion = lambda x, y: x if x <= y else y
    for primo in descPrimosNumGenerador:
        if primo in dicDescomposicionPrimosGrupo:
            listaPrimosComunes.append(
                pow(primo, menorRepeticion(descPrimosNumGenerador[primo], dicDescomposicionPrimosGrupo[primo])) )
    for primo in listaPrimosComunes:
        mcd = mcd * primo
    return mcd

In [106]:
def generadorTotient(numGenerador):
    strIndice = ""
    mcd = calcularMCDconGrupo(numGenerador)
    for digit in str(numGenerador):
        strIndice = strIndice + imprimirSuperIndice(int(digit))
    if mcd == 1:
        print("< a" + strIndice + "> = " + bold("--- Grupo Cíclico de G ---"))
        return True
    else:
        if mcd == numGenerador or mcd == 1:
            print("< a" + strIndice + "> = " + "Subgrupo Cíclico generado por si MISMO")
        else:
            print("< a" + strIndice + "> = " + "Subgrupo Cíclico generado por " + str(mcd))

        return False

In [107]:
def imprimirMetodoTotient():
    print("                                   " + bold("Orden del Grupo G: " + str(n)) + "\n")
    print(bold("→ Generadores Cíclicos de G:"))
    print(bold("|") + " { " + ', '.join(str(x) for x in GeneradoresGCiclico) + " } " + bold("|" + " = " + str(numGeneradoresGCiclico))+ "\n")

    print("Tiempo de ejecución del " + bold("Metodo Totient de Euler") + ": " + str(Tiempo1) + " segundos.")
    print(bold("→ Número de Generadores Cíclicos de G: --- φ(" + str(n) + ") = " + str(numGeneradoresGCiclico) + " ---"))
    print("→ Por este Metodo, no se obtiene los elementos de los SubGrupos generados por G.")

###### Ejecutar el Metodo del Totient:

In [108]:
GeneradoresGCiclico = []
numGeneradoresGCiclico=0
inicio1 = time.time()

for num in Grupo:
    if generadorTotient(num):
        numGeneradoresGCiclico+=1
        GeneradoresGCiclico.append(num)

fin1 = time.time()
Tiempo1 = round(fin1-inicio1,2)

imprimirMetodoTotient()

< a¹> = --- Grupo Cíclico de G ---
< a²> = Subgrupo Cíclico generado por si MISMO
< a³> = --- Grupo Cíclico de G ---
< a⁴> = Subgrupo Cíclico generado por si MISMO
< a⁵> = Subgrupo Cíclico generado por si MISMO
< a⁶> = Subgrupo Cíclico generado por 2
< a⁷> = --- Grupo Cíclico de G ---
< a⁸> = Subgrupo Cíclico generado por si MISMO
< a⁹> = --- Grupo Cíclico de G ---
< a¹⁰> = Subgrupo Cíclico generado por si MISMO
< a¹¹> = --- Grupo Cíclico de G ---
< a¹²> = Subgrupo Cíclico generado por 4
< a¹³> = --- Grupo Cíclico de G ---
< a¹⁴> = Subgrupo Cíclico generado por 2
< a¹⁵> = Subgrupo Cíclico generado por 5
< a¹⁶> = Subgrupo Cíclico generado por si MISMO
< a¹⁷> = --- Grupo Cíclico de G ---
< a¹⁸> = Subgrupo Cíclico generado por 2
< a¹⁹> = --- Grupo Cíclico de G ---
< a²⁰> = Subgrupo Cíclico generado por si MISMO
< a²¹> = --- Grupo Cíclico de G ---
< a²²> = Subgrupo Cíclico generado por 2
< a²³> = --- Grupo Cíclico de G ---
< a²⁴> = Subgrupo Cíclico generado por 8
< a²⁵> = Subgrupo Cíclico 

### Metodo Tradicional:
##### Comprobar si el subgrupo generado por cada elemento es el Grupo Cíclico de G.

In [109]:
###### Se calcula cada subgrupo generado por cada elemento (y se almacena en un Set). Luego, se comprueba su tamaño:

In [110]:
def generador(numGenerador):
    SubGrupo = set()
    for indice in Grupo:
        SubGrupo.add(indice * numGenerador % n)
        if indice * numGenerador % n == 0:
            break
    strIndice = imprimirSuperIndice(numGenerador)
    if len(SubGrupo) == len(Grupo):
        print("< a" + strIndice + "> = " + bold("--- Grupo Cíclico de G ---"))
        return True
    else:
        mcd = calcularMCDconGrupo(numGenerador)
        if mcd == numGenerador or mcd == 1:
            print("< a" + strIndice + "> = ", end="")
            print(SubGrupo)
        else:
            print("< a" + strIndice + "> = " + "Subgrupo Cíclico generado por " + str(mcd))

        return False

In [111]:
def imprimirMetodoTradicional():
    print("                                   " + bold("Orden del Grupo G: " + str(n)) + "\n")
    print(bold("→ Generadores Cíclicos de G:"))
    print(bold("|") + " { " + ', '.join(str(x) for x in GeneradoresGCiclico) + " } " + bold("|" + " = " + str(numGeneradoresGCiclico))+ "\n")

    print("Tiempo de ejecución del " + bold("Metodo Tradicional") + ": " + str(Tiempo1) + " segundos.")
    print(bold("→ Número de Generadores Cíclicos de G: --- φ(" + str(n) + ") = " + str(numGeneradoresGCiclico) + " ---"))

###### Ejecutar el Método Tradicional:

In [ ]:
GeneradoresGCiclico = []
numGeneradoresGCiclico=0
inicio1 = time.time()

for num in Grupo:
    if generador(num):
        numGeneradoresGCiclico+=1
        GeneradoresGCiclico.append(num)

fin1 = time.time()
Tiempo1 = round(fin1-inicio1,2)

imprimirMetodoTradicional()

< a¹> = --- Grupo Cíclico de G ---
< a²> = {0, 2, 4, 6, 8, 10, 12, 14, 16, 18, 20, 22, 24, 26, 28, 30, 32, 34, 36, 38, 40, 42, 44, 46, 48, 50, 52, 54, 56, 58, 60, 62, 64, 66, 68, 70, 72, 74, 76, 78, 80, 82, 84, 86, 88, 90, 92, 94, 96, 98, 100, 102, 104, 106, 108, 110, 112, 114, 116, 118, 120, 122, 124, 126, 128, 130, 132, 134, 136, 138, 140, 142, 144, 146, 148, 150, 152, 154, 156, 158, 160, 162, 164, 166, 168, 170, 172, 174, 176, 178, 180, 182, 184, 186, 188, 190, 192, 194, 196, 198, 200, 202, 204, 206, 208, 210, 212, 214, 216, 218, 220, 222, 224, 226, 228, 230, 232, 234, 236, 238, 240, 242, 244, 246, 248, 250, 252, 254, 256, 258, 260, 262, 264, 266, 268, 270, 272, 274, 276, 278, 280, 282, 284, 286, 288, 290, 292, 294, 296, 298, 300, 302, 304, 306, 308, 310, 312, 314, 316, 318, 320, 322, 324, 326, 328, 330, 332, 334, 336, 338, 340, 342, 344, 346, 348, 350, 352, 354, 356, 358, 360, 362, 364, 366, 368, 370, 372, 374, 376, 378, 380, 382, 384, 386, 388, 390, 392, 394, 396, 398, 400, 402, 4

In [ ]:
##### Muchas Gracias. Desarrollado por David Santiago Cruz Hernandez. Correo: dcruzhe@unal.edu.co